In [20]:
import torch.optim as optim

from torch.autograd import Variable


from IPython.display import clear_output

import fedlern.utils as u
from fedlern.train_utils import *
from fedlern.models.resnet import ResNet18
from fedlern.quantize import quantize
from tqdm.notebook import tqdm

In [22]:


def get_model2(model, learning_rate=1e-3, weight_decay=1e-4):

    # set the first layer not trainable
    # model.features.conv0.weight.requires_grad = False

    # all fc layers
    weights = [
        p for n, p in model.named_parameters()
        if 'weight' in n and 'conv' not in n
    ]

    # all conv layers
    weights_to_be_quantized = [
        p for n, p in model.named_parameters()
        # if 'conv' in n and 'conv0' not in n
        if 'conv' in n and 'weight' in n
    ]

    biases = [
        p for n, p in model.named_parameters()
        if 'bias' in n
    ]    

    params = [
        {'params': weights, 'weight_decay': weight_decay},
        {'params': weights_to_be_quantized, 'weight_decay': weight_decay},
        {'params': biases,  'weight_decay': weight_decay}
    ]
    optimizer = optim.SGD(params, lr=learning_rate, momentum=0.9)

    loss = nn.CrossEntropyLoss().cuda()
    model = model.cuda()  # move the model to gpu
    return model, loss, optimizer
def quantize_bw(kernel : torch.Tensor):
    """
    binary quantization
    Return quantized weights of a layer.
    """
    delta = kernel.abs().mean()
    sign = kernel.sign().float()



    return sign*delta

In [23]:
# Device configuration
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Hyper-parameters
stats = (0.49139968, 0.48215841, 0.44653091), (0.24703223, 0.24348513, 0.26158784)
batch_size_test = 250
batch_size_train = 128

quantize_nbits = [8,4,2]
num_epochs = 200
learning_rate = 0.001
eta_rate = 1.05
eta = 1
global best_acc
best_acc = 0
best_count = 0

In [24]:
train_loader, test_loader = prepare_dataloader_cifar(num_workers=8, 
                                                     train_batch_size=batch_size_train, 
                                                     eval_batch_size=batch_size_test, 
                                                     stats=stats)

    

Files already downloaded and verified


In [25]:
net = ResNet18()
net.to(device)


ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (shortcut): Sequential()
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=

In [17]:
net, criterion, optimizer = get_model2(net, learning_rate=0.1, weight_decay=5e-4)

    
all_G_kernels = [
    Variable(kernel.data.clone(), requires_grad=True)
    for kernel in optimizer.param_groups[1]['params']
]


all_W_kernels = [kernel for kernel in optimizer.param_groups[1]['params']]
kernels = [{'params': all_G_kernels}]
optimizer_quant = optim.SGD(kernels, lr=0)

scheduler = optim.lr_scheduler.MultiStepLR(optimizer, milestones=[80,120,160], gamma=0.1)

In [14]:

#for epoch in tqdm(range(num_epochs)):    num_epochs = 200
for epoch in (pbar := tqdm(range(num_epochs))):
    #print('Epoch ID', epoch)
    #----------------------------------------------------------------------
    # Training
    #----------------------------------------------------------------------
    pbar.set_description(f"Training {epoch}",refresh=True)
    correct = 0; total = 0; train_loss = 0
    net.train()
    for batch_idx, (x, target) in enumerate(tqdm(train_loader, leave=False)):
    #for batch_idx, (x, target) in enumerate(train_loader):
        #if batch_idx < 1:
        optimizer.zero_grad()
        x, target = Variable(x.cuda()), Variable(target.cuda())
        all_W_kernels = optimizer.param_groups[1]['params']
        all_G_kernels = optimizer_quant.param_groups[0]['params']
        
        for i in range(len(all_W_kernels)):
            k_W = all_W_kernels[i]
            k_G = all_G_kernels[i]
            V = k_W.data
            #print(type(V))
            #####Binary Connect#########################
            #k_G.data = quantize_bw(V)
            ############################################
            
            ######Binary Relax##########################
            if epoch<120:
                #k_G.data = (eta*quantize_bw(V)+V)/(1+eta)
                k_G.data = (eta*quantize(V,num_bits=quantize_nbits)+V)/(1+eta)
                
            else:
                k_G.data = quantize(V, num_bits=quantize_nbits)
            #############################################
            
            k_W.data, k_G.data = k_G.data, k_W.data
            
            
        score = net(x)
        loss = criterion(score, target)
        loss.backward()
        
        for i in range(len(all_W_kernels)):
            k_W = all_W_kernels[i]
            k_G = all_G_kernels[i]
            k_W.data, k_G.data = k_G.data, k_W.data
        
        optimizer.step()
        
        train_loss += loss.data
        _, predicted = torch.max(score.data, 1)
        total += target.size(0)
        correct += predicted.eq(target.data).cpu().sum()
        pbar.write(f"Training {batch_idx} Loss: {train_loss/(batch_idx+1):.3f} | Acc: {100.*correct/total:.3f}% ({correct}/{total})")
        
    #----------------------------------------------------------------------
    # Testing
    #----------------------------------------------------------------------
    pbar.set_description(f"Testing {epoch}",refresh=True)
    test_loss = 0; correct = 0; total = 0
    net.eval()
    
    for i in range(len(all_W_kernels)):
        k_W = all_W_kernels[i]
        k_quant = all_G_kernels[i]    
        k_W.data, k_quant.data = k_quant.data, k_W.data
    with torch.no_grad():
        for batch_idx, (x, target) in enumerate(tqdm(test_loader, leave=False)):
        #for batch_idx, (x, target) in enumerate(test_loader):
            x, target = Variable(x.cuda()), Variable(target.cuda())
            score= net(x)
            
            loss = criterion(score, target)
            test_loss += loss.data
            _, predicted = torch.max(score.data, 1)
            total += target.size(0)
            correct += predicted.eq(target.data).cpu().sum()
            pbar.write(f"Testing {batch_idx} Loss: {train_loss/(batch_idx+1):.3f} | Acc: {100.*correct/total:.3f}% ({correct}/{total})")

    
    #----------------------------------------------------------------------
    # Save the checkpoint
    #----------------------------------------------------------------------
    '''
    for i in range(len(all_W_kernels)):
        k_W = all_W_kernels[i]
        k_quant = all_G_kernels[i]    
        k_W.data, k_quant.data = k_quant.data, k_W.data
        '''  
    acc = 100.*correct/total
    #if acc > best_acc:
    if correct > best_count:
        # print('Saving model...')
        # state = {
        #     'state': net.state_dict(), #net,
        #     'acc': acc,
        #     'epoch': epoch,
        # }
        
        # torch.save(state, f'./saved_models/resnet_{quantize_nbits}bits_{u.time_stamp()}.pth')
        #net.save_state_dict('resnet20.pt')
        best_acc = acc
        best_count = correct

    for i in range(len(all_W_kernels)):
        k_W=all_W_kernels[i]
        k_quant=all_W_kernels[i]
        k_W.data, k_quant.data =k_quant.data,k_W.data
    clear_output(wait=True)
    
save_model(net, "saved_models", f'resnet_{quantize_nbits}bits_{u.time_stamp()}.pth')

  0%|          | 0/200 [00:00<?, ?it/s]

  0%|          | 0/391 [00:00<?, ?it/s]

Training 0 Loss: 2.462 | Acc: 8.594% (11/128)
Training 1 Loss: 2.728 | Acc: 9.766% (25/256)
Training 2 Loss: 3.022 | Acc: 11.979% (46/384)
Training 3 Loss: 3.407 | Acc: 11.719% (60/512)
Training 4 Loss: 3.994 | Acc: 12.188% (78/640)
Training 5 Loss: 4.469 | Acc: 11.849% (91/768)
Training 6 Loss: 5.256 | Acc: 12.054% (108/896)
Training 7 Loss: 6.235 | Acc: 12.891% (132/1024)
Training 8 Loss: 6.830 | Acc: 12.674% (146/1152)
Training 9 Loss: 7.035 | Acc: 12.266% (157/1280)
Training 10 Loss: 6.909 | Acc: 12.074% (170/1408)
Training 11 Loss: 6.848 | Acc: 11.979% (184/1536)
Training 12 Loss: 6.742 | Acc: 12.139% (202/1664)
Training 13 Loss: 6.503 | Acc: 11.998% (215/1792)
Training 14 Loss: 6.301 | Acc: 12.292% (236/1920)
Training 15 Loss: 6.188 | Acc: 12.402% (254/2048)
Training 16 Loss: 5.984 | Acc: 12.316% (268/2176)
Training 17 Loss: 5.801 | Acc: 12.283% (283/2304)
Training 18 Loss: 5.637 | Acc: 12.336% (300/2432)
Training 19 Loss: 5.513 | Acc: 12.188% (312/2560)
Training 20 Loss: 5.368 |

  0%|          | 0/40 [00:00<?, ?it/s]

Testing 0 Loss: 843.478 | Acc: 32.800% (82/250)
Testing 1 Loss: 421.739 | Acc: 33.400% (167/500)
Testing 2 Loss: 281.159 | Acc: 31.867% (239/750)
Testing 3 Loss: 210.869 | Acc: 32.400% (324/1000)
Testing 4 Loss: 168.696 | Acc: 32.400% (405/1250)
Testing 5 Loss: 140.580 | Acc: 32.333% (485/1500)
Testing 6 Loss: 120.497 | Acc: 32.171% (563/1750)
Testing 7 Loss: 105.435 | Acc: 32.000% (640/2000)
Testing 8 Loss: 93.720 | Acc: 32.267% (726/2250)
Testing 9 Loss: 84.348 | Acc: 32.520% (813/2500)
Testing 10 Loss: 76.680 | Acc: 32.473% (893/2750)
Testing 11 Loss: 70.290 | Acc: 32.433% (973/3000)
Testing 12 Loss: 64.883 | Acc: 32.677% (1062/3250)
Testing 13 Loss: 60.248 | Acc: 33.029% (1156/3500)
Testing 14 Loss: 56.232 | Acc: 33.173% (1244/3750)
Testing 15 Loss: 52.717 | Acc: 33.200% (1328/4000)
Testing 16 Loss: 49.616 | Acc: 33.082% (1406/4250)
Testing 17 Loss: 46.860 | Acc: 33.156% (1492/4500)
Testing 18 Loss: 44.394 | Acc: 32.989% (1567/4750)
Testing 19 Loss: 42.174 | Acc: 32.900% (1645/5000

...

Testing 0 Loss: 120.202 | Acc: 87.200% (218/250)
Testing 1 Loss: 60.101 | Acc: 85.400% (427/500)
Testing 2 Loss: 40.067 | Acc: 85.600% (642/750)
Testing 3 Loss: 30.050 | Acc: 85.600% (856/1000)
Testing 4 Loss: 24.040 | Acc: 85.840% (1073/1250)
Testing 5 Loss: 20.034 | Acc: 85.867% (1288/1500)
Testing 6 Loss: 17.172 | Acc: 85.314% (1493/1750)
Testing 7 Loss: 15.025 | Acc: 85.200% (1704/2000)
Testing 8 Loss: 13.356 | Acc: 85.067% (1914/2250)
Testing 9 Loss: 12.020 | Acc: 85.080% (2127/2500)
Testing 10 Loss: 10.927 | Acc: 85.018% (2338/2750)
Testing 11 Loss: 10.017 | Acc: 85.233% (2557/3000)
Testing 12 Loss: 9.246 | Acc: 85.169% (2768/3250)
Testing 13 Loss: 8.586 | Acc: 85.057% (2977/3500)
Testing 14 Loss: 8.013 | Acc: 85.040% (3189/3750)
Testing 15 Loss: 7.513 | Acc: 85.125% (3405/4000)
Testing 16 Loss: 7.071 | Acc: 85.200% (3621/4250)
Testing 17 Loss: 6.678 | Acc: 85.289% (3838/4500)
Testing 18 Loss: 6.326 | Acc: 85.347% (4054/4750)
Testing 19 Loss: 6.010 | Acc: 85.380% (4269/5000)
Test

  0%|          | 0/391 [00:00<?, ?it/s]

Training 0 Loss: 0.245 | Acc: 91.406% (117/128)
Training 1 Loss: 0.239 | Acc: 91.406% (234/256)
Training 2 Loss: 0.259 | Acc: 91.146% (350/384)
Training 3 Loss: 0.245 | Acc: 91.992% (471/512)
Training 4 Loss: 0.270 | Acc: 91.406% (585/640)
Training 5 Loss: 0.282 | Acc: 91.146% (700/768)
Training 6 Loss: 0.289 | Acc: 90.960% (815/896)
Training 7 Loss: 0.290 | Acc: 90.625% (928/1024)
Training 8 Loss: 0.274 | Acc: 91.146% (1050/1152)
Training 9 Loss: 0.280 | Acc: 90.781% (1162/1280)
Training 10 Loss: 0.277 | Acc: 90.980% (1281/1408)
Training 11 Loss: 0.277 | Acc: 90.885% (1396/1536)
Training 12 Loss: 0.277 | Acc: 90.865% (1512/1664)
Training 13 Loss: 0.276 | Acc: 90.681% (1625/1792)
Training 14 Loss: 0.282 | Acc: 90.469% (1737/1920)
Training 15 Loss: 0.283 | Acc: 90.381% (1851/2048)
Training 16 Loss: 0.279 | Acc: 90.625% (1972/2176)
Training 17 Loss: 0.276 | Acc: 90.755% (2091/2304)
Training 18 Loss: 0.276 | Acc: 90.707% (2206/2432)
Training 19 Loss: 0.276 | Acc: 90.781% (2324/2560)
Train

  0%|          | 0/40 [00:00<?, ?it/s]

Testing 0 Loss: 119.913 | Acc: 82.800% (207/250)
Testing 1 Loss: 59.956 | Acc: 82.800% (414/500)
Testing 2 Loss: 39.971 | Acc: 85.067% (638/750)
Testing 3 Loss: 29.978 | Acc: 84.200% (842/1000)
Testing 4 Loss: 23.983 | Acc: 84.640% (1058/1250)
Testing 5 Loss: 19.985 | Acc: 84.867% (1273/1500)
Testing 6 Loss: 17.130 | Acc: 85.086% (1489/1750)
Testing 7 Loss: 14.989 | Acc: 84.800% (1696/2000)
Testing 8 Loss: 13.324 | Acc: 84.756% (1907/2250)
Testing 9 Loss: 11.991 | Acc: 84.640% (2116/2500)
Testing 10 Loss: 10.901 | Acc: 84.364% (2320/2750)
Testing 11 Loss: 9.993 | Acc: 84.667% (2540/3000)
Testing 12 Loss: 9.224 | Acc: 84.646% (2751/3250)
Testing 13 Loss: 8.565 | Acc: 84.571% (2960/3500)
Testing 14 Loss: 7.994 | Acc: 84.587% (3172/3750)
Testing 15 Loss: 7.495 | Acc: 84.625% (3385/4000)
Testing 16 Loss: 7.054 | Acc: 84.824% (3605/4250)
Testing 17 Loss: 6.662 | Acc: 85.067% (3828/4500)
Testing 18 Loss: 6.311 | Acc: 84.905% (4033/4750)
Testing 19 Loss: 5.996 | Acc: 84.940% (4247/5000)
Testi